<div style="font-size:22pt; line-height:25pt; font-weight:bold; text-align:center;">Parameterized PDE</div>

The aim of this notebook is to find the way to estimate the result of a parameterized PDE problem with a group of pre-computed results, so that the computation time can be cut down. There are 2 methods tested, the PINN in DeepXDE toolbox and also the POD method.
1. [Reference solution](#ref)
2. [PINN](#pinn)
    1. [DeepXDE](#dde)
3. [POD](#pod)
    1. [POD-Greddy Algorithm](#pod_ga)
    2. [POD-TensorFlow Version I](#tf1)
    3. [POD-TensorFlow Version II](#tf2)
4. [Gaussian Processe](#gp)

In [1]:
import deepxde
import numpy as np
import tensorflow as tf
import itertools
import matplotlib.pyplot as plt
from matplotlib import cm
import seaborn as sns
import scipy as sp
from datetime import datetime 
import numpy as np
import timeit
from sklearn.externals import joblib
import shutil
from pyDOE import lhs

from gaussian_process import GaussianProcess

import ipywidgets
from IPython.display import display

/Users/ydli/anaconda3/lib/python3.7/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


# <a id="ref"></a> 1. Reference solution

The Steady Advection-Diffusion problem applied in a closed domain with non-homogeneous Dirichlet boundary conditions is chossen to test the different methods:
$$\mathbf{u}\bullet\nabla T-\kappa\bullet\Delta T=0$$

The range of parameters are:
$$\begin{cases}\mathbf{x}=(x,y)\in[0,1]\times[0,1]\\
\mathbf{u}=\left[\begin{matrix}u \cr 0\end{matrix}\right], u\in[0,0.5]
\\\kappa\in[0.0005,0.025]\end{cases}$$

The boundary conditions of the problem are:
$$\begin{cases}T((x,y)\in\Gamma_D)=T_D(y,\bar{y})
\\\nabla T((x,y)\in\Gamma_N)\bullet\mathbf{n(\mathbf{x})}=0\end{cases}$$

With the non-homogeneous boundary temperature defined as below:
$$T_D(y,\bar{y})=\begin{cases}300, y\in[0,\frac{1}{3}]
\\300+325(sin(3\pi |y-\bar{y}|)+1), y\in[\frac{1}{3},\frac{2}{3}]
\\300, y\in[\frac{2}{3},1]\end{cases}\\\bar{y}\in[0.4,0.6]$$

The refernce solution is computed by finite difference. It has been solved for a mesh of $61\times 61$ elements.

In [8]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

Nx = 61
Ny = 61
xmin = 0
xmax = 1
ymin = 0
ymax = 1
x  = np.linspace(xmin, xmax, Nx)
y  = np.linspace(xmin, xmax, Ny)

dx = x[1]-x[0]
dy = y[1]-y[0]

In [9]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

def computeA1(Nx,Ny,dx,dy):
    D2x=np.zeros([Nx-2,Nx-2])
    D2y=np.zeros([Ny-2,Ny-2])
    for i in range(Nx-2):
        D2x[i][i]=-2/dx**2
        D2y[i][i]=-2/dy**2
        if i>0:
            D2x[i-1][i]=1/dx**2
            D2x[i][i-1]=1/dx**2
            D2y[i-1][i]=1/dy**2
            D2y[i][i-1]=1/dy**2

    D2x[Nx-3,Nx-3] = -1/dx**2

    D2y[Nx-3,Nx-3] = -1/dy**2
    D2y[0,0] = -1/dy**2

    A1 = np.kron(D2x,np.eye(Ny-2)) + np.kron(np.eye(Nx-2),D2y)
    return A1

def computeA2(Nx,Ny,dx):
    D1x=np.zeros((Nx-2,Nx-2))
    for i in range(Nx-2):
        D1x[i][i]=1/dx
        if i>0:
            D1x[i][i-1]=-1/dx

    A2 = np.kron(D1x,np.eye(Ny-2))
    return A2

def computeb1(u,kappa,ybar,Ny, Ly, dx, y, Ti, Tleft):
    TleftBC = np.zeros((Ny-2,1))
    b1 = np.zeros((Ny-2,1))
    for i in range(1,Ny-1):
        if y[i]<Ly/3:
            TleftBC[i-1,0] = Ti
            b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
        else:
            if y[i]>2*Ly/3:
                TleftBC[i-1,0] = Ti
                b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
            else:
                TleftBC[i-1,0] = Ti+(Tleft-Ti)*(np.sin(np.pi*np.abs(y[i]-ybar)/(1/3))+1)/2
                b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
    return b1,TleftBC
    
def buildAdvectionDiffusionOperators(u,kappa,ybar,Nx,Ny,dx,dy, Ly, y, Ti=300, Tleft=950):
    if u<0:
        print('Error: u should be positive')
        return None
    
    b1,TleftBC= computeb1(u,kappa,ybar,Ny, Ly, dx, y, Ti, Tleft)
    b = np.vstack([b1,np.zeros(((Nx-3)*(Ny-2),1))])

    A2 = computeA2(Nx,Ny,dx)

    A1 = computeA1(Nx,Ny,dx,dy)

    A = kappa*A1-u*A2
    return A,b,TleftBC

In [10]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

def EF(u,k,ybar,Nx=61,Ny=61,dx=1/60,dy=1/60, Ly=1, y=np.linspace(0, 1, Ny), Ti=300, Tleft=950):
    tic = timeit.default_timer()
    A,b,TleftBC = buildAdvectionDiffusionOperators(u,k,ybar,Nx,Ny,dx,dy,Ly,y,Ti,Tleft)
    res = sp.linalg.solve(A,b)
    toc = timeit.default_timer()
    res=res.reshape(59,59).T
    res=np.hstack([res,np.array([res[:,-1]]).T])
    res=np.hstack([TleftBC,res])
    res=np.vstack([res[0,:],res])
    res=np.vstack([res,res[-1,:]])
    time=(toc-tic)/60.
    #print("COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    return res, time

In [14]:
u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
# v = ipywidgets.FloatSlider(value=0,min=0,max=0.5,step=0.01,description='v:',
#                            disabled=False,continuous_update=False,orientation='horizontal',
#                            readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0.0005,max=0.025,step=0.0005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.4f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.6,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])

def f1(u, k, ybar):
    T, time = EF(u,k,ybar,Nx,Ny,dx,dy, 1, y, Ti=300, Tleft=950)
    print("COMPUTATION TIME: "+str(time)+" min")
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('DeepXDE (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    #print((u, k, ybar))

out = ipywidgets.interactive_output(f1, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

The reference computation time is around 8 sec.

# <a id="pinn"></a> 2. PINN

PINN which means the physics-informed neural networks, embeds a PDE into the loss of the neural network using automatic differentiation. It offers a mesh free method to resolve the PDE problem.

## <a id="dde"></a> 2.1 DeepXDE

This section uses the PINN offered by DeepXDE toolbox to solve the problem.

In the training step, 20 groups of parameters $(u,\kappa,\bar{y})$ are uniformly chossen from the parameters domain $[0,0.5]\times[0.0005,0.025]\times[0.4,0.6]$. For each group of parameters, one Neural Network is constructed to solve the corresponding PDE. The values in a $61\times 61$ mesh are computed by the trained networks. Then the groups of parameters together with the corresponding mesh solutions are sent to a estimator.

**To use PINN, we have to know the structure of the PDE problem.**

In [26]:
class PINN(object):
    def __init__(self):
        self.geom = deepxde.geometry.Rectangle([0, 0], [1, 1])
        self.num_domain=1200
        self.num_boundary=120
        self.num_test=150
        self.u=0
        self.v=0
        self.k=0
        self.ybar=0
        self.model=None
        x = np.linspace(0, 1, 61)
        y = np.linspace(0, 1, 61)
        self.X,self.Y = np.meshgrid(x,y)
        
    def pde(self, x, f):
        dx = tf.gradients(f, x)[0]
        dx, dy = dx[:, 0], dx[:, 1]
        dxx = tf.gradients(dx, x)[0][:, 0]
        dyy = tf.gradients(dy, x)[0][:, 1]
        return self.u*dx+self.v*dx-self.k*dxx-self.k*dyy

    def boundary1(self, x, on_boundary):
        return on_boundary and np.isclose(x[0], 0)

    def boundary2(self, x, on_boundary):
        return on_boundary and not np.isclose(x[0], 0)

    def func1(self, x):
        return 300*np.ones([len(x), 1])+325*(x[:,1:2]>=1/3)*(x[:,1:2]<2/3)*(np.sin(3*np.pi * np.abs(x[:, 1:2]-self.ybar))+1)

    def func2(self, x):
        return np.zeros([len(x), 1]) 
    
    def fit(self, u, v, k, ybar):
        self.u=u
        self.v=v
        self.k=k
        self.ybar=ybar
        bc1 = deepxde.DirichletBC(self.geom, self.func1, self.boundary1)
        bc2 = deepxde.NeumannBC(self.geom, self.func2, self.boundary2)

        data = deepxde.data.PDE(self.geom, 1, self.pde, [bc1,bc2], 
                                num_domain=self.num_domain, num_boundary=self.num_boundary, 
                                num_test=self.num_test,train_distribution = "uniform")
        net = deepxde.maps.FNN([2] + [32] * 2 + [1], "tanh", "Glorot uniform")
        self.model = deepxde.Model(data, net)
        
    def fit(self, u, k, ybar):
        self.u=u
        #self.v=v
        self.k=k
        self.ybar=ybar
        bc1 = deepxde.DirichletBC(self.geom, self.func1, self.boundary1)
        bc2 = deepxde.NeumannBC(self.geom, self.func2, self.boundary2)

        data = deepxde.data.PDE(self.geom, 1, self.pde, [bc1,bc2], 
                                num_domain=self.num_domain, num_boundary=self.num_boundary, 
                                num_test=self.num_test,train_distribution = "uniform")
        net = deepxde.maps.FNN([2] + [32] * 2 + [1], "tanh", "Glorot uniform")
        self.model = deepxde.Model(data, net)
    
    def train(self,epochs=50000):
        self.model.compile("adam", lr=0.001)
        losshistory, train_state=self.model.train(epochs=epochs)
        #deepxde.saveplot(losshistory, train_state, issave=True, isplot=True)
        
    def predict(self):
        resPINN=np.zeros((self.X.shape[0],self.X.shape[1]))
        for i in range(self.X.shape[0]):
            for j in range(self.X.shape[1]):
                resPINN[i][j]=self.model.predict([[self.X[i][j],self.Y[i][j]]])
        return resPINN

In [36]:
def uniform_p(pmin,pmax, n):
    n1 = int(np.ceil(n ** (1 / 3)))
    pi = []
    for i in range(pmax.shape[0]):
        pi.append(np.linspace(pmin[i], pmax[i], num=n1))
    p = np.array(list(itertools.product(*pi)),dtype="float32")
    if n != len(p):
        print(
            "Warning: {} points required, but {} points sampled.".format(n, len(p))
        )
    return p

In [28]:
pMin_i = np.array([0.,0.0005,0.4])
pMax_i = np.array([0.5,0.025,0.6])
pMin = np.zeros((3,1))
pMin[:,0]= pMin_i[:]
pMax = np.zeros((3,1))
pMax[:,0]= pMax_i[:]
l=61*61

nSamples=20
#nParam = len(pMin)
#pCandidate = np.dot(pMin,np.ones((1,nSamples))) + lhs(nParam,nSamples).T*np.dot((pMax-pMin),np.ones((1,nSamples)))
pCandidate=uniform_p(pMin,pMax,nSamples)[:,:,0]
nSamples=len(pCandidate)

In [29]:
tic = timeit.default_timer()
model=PINN()
res=np.zeros((l,nSamples))
for i in range(nSamples):
    model.fit(pCandidate[i,0],pCandidate[i,1],pCandidate[i,2])
    model.train(epochs=49000)
    res[:,i]=model.predict().reshape(l,1)[:,0]
    #print("########"+str(i)+"########")
mean = "constant"
covariance = "squared_exponential"
theta_U = np.array([100000.0]*3)
theta_L = np.array([0.001]*3)
theta_0 = np.array([1.0]*3)
GP = GaussianProcess(regr = mean, corr = covariance,theta0 = theta_0,thetaL = theta_L, thetaU = theta_U)
GP.fit(pCandidate, res.T)
joblib.dump(GP, "../results/Offline/GP_p3.pkl")
    
toc = timeit.default_timer()
print("OFFLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")

Building feed-forward neural network...
Instructions for updating:
Use keras.layers.dense instead.
Instructions for updating:
Colocations handled automatically by placer.
'build' took 0.047770 s

Compiling model...
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Use tf.cast instead.
'compile' took 0.692895 s

Initializing variables...
Training model...

Step      Train loss                        Test loss                         Test metric
0         [5.08e-10, 2.87e+05, 2.31e-02]    [5.24e-10, 0.00e+00, 0.00e+00]    []  
1000      [2.49e-07, 2.48e+05, 2.10e-02]    [4.66e-07, 0.00e+00, 0.00e+00]    []  
2000      [2.97e-08, 2.22e+05, 2.18e-03]    [5.99e-08, 0.00e+00, 0.00e+00]    []  
3000      [7.15e-09, 1.98e+05, 4.95e-04]    [1.50e-08, 0.00e+00, 0.00e+00]    []  
4000      [2.30e-09, 1.77e+05, 1.54e-04]    [4.96e-09, 0.00e+00, 0.00e+00]    []  
5000      [8.78e-10, 1.57e+05, 5.69e-05]    [1.93e-09, 0.00e+00, 0.00e+00]    []  
6000      [3.76e-10, 1.40e+05

Predicting...
'predict' took 0.000330 s

Predicting...
'predict' took 0.000407 s

Predicting...
'predict' took 0.000341 s

Predicting...
'predict' took 0.000395 s

Predicting...
'predict' took 0.000331 s

Predicting...
'predict' took 0.000507 s

Predicting...
'predict' took 0.000333 s

Predicting...
'predict' took 0.000527 s

Predicting...
'predict' took 0.000517 s

Predicting...
'predict' took 0.000351 s

Predicting...
'predict' took 0.000325 s

Predicting...
'predict' took 0.000355 s

Predicting...
'predict' took 0.000394 s

Predicting...
'predict' took 0.000372 s

Predicting...
'predict' took 0.000309 s

Predicting...
'predict' took 0.000393 s

Predicting...
'predict' took 0.000396 s

Predicting...
'predict' took 0.000380 s

Predicting...
'predict' took 0.000331 s

Predicting...
'predict' took 0.000322 s

Predicting...
'predict' took 0.000317 s

Predicting...
'predict' took 0.000320 s

Predicting...
'predict' took 0.000307 s

Predicting...
'predict' took 0.000323 s

Predicting...
'p

Predicting...
'predict' took 0.000425 s

Predicting...
'predict' took 0.000608 s

Predicting...
'predict' took 0.000371 s

Predicting...
'predict' took 0.000374 s

Predicting...
'predict' took 0.000365 s

Predicting...
'predict' took 0.000487 s

Predicting...
'predict' took 0.000367 s

Predicting...
'predict' took 0.000407 s

Predicting...
'predict' took 0.000298 s

Predicting...
'predict' took 0.000402 s

Predicting...
'predict' took 0.000311 s

Predicting...
'predict' took 0.000304 s

Predicting...
'predict' took 0.000344 s

Predicting...
'predict' took 0.000366 s

Predicting...
'predict' took 0.000398 s

Predicting...
'predict' took 0.000368 s

Predicting...
'predict' took 0.000313 s

Predicting...
'predict' took 0.000389 s

Predicting...
'predict' took 0.000324 s

Predicting...
'predict' took 0.000365 s

Predicting...
'predict' took 0.000341 s

Predicting...
'predict' took 0.000332 s

Predicting...
'predict' took 0.000341 s

Predicting...
'predict' took 0.000320 s

Predicting...
'p

Predicting...
'predict' took 0.000425 s

Predicting...
'predict' took 0.000578 s

Predicting...
'predict' took 0.000451 s

Predicting...
'predict' took 0.000585 s

Predicting...
'predict' took 0.000550 s

Predicting...
'predict' took 0.000706 s

Predicting...
'predict' took 0.000699 s

Predicting...
'predict' took 0.000790 s

Predicting...
'predict' took 0.000660 s

Predicting...
'predict' took 0.000628 s

Predicting...
'predict' took 0.000695 s

Predicting...
'predict' took 0.000771 s

Predicting...
'predict' took 0.000838 s

Predicting...
'predict' took 0.000693 s

Predicting...
'predict' took 0.000578 s

Predicting...
'predict' took 0.000746 s

Predicting...
'predict' took 0.000610 s

Predicting...
'predict' took 0.000436 s

Predicting...
'predict' took 0.000533 s

Predicting...
'predict' took 0.000763 s

Predicting...
'predict' took 0.000540 s

Predicting...
'predict' took 0.000509 s

Predicting...
'predict' took 0.000664 s

Predicting...
'predict' took 0.000639 s

Predicting...
'p

Predicting...
'predict' took 0.000529 s

Predicting...
'predict' took 0.000416 s

Predicting...
'predict' took 0.000509 s

Predicting...
'predict' took 0.000437 s

Predicting...
'predict' took 0.000484 s

Predicting...
'predict' took 0.000426 s

Predicting...
'predict' took 0.000472 s

Predicting...
'predict' took 0.000413 s

Predicting...
'predict' took 0.000550 s

Predicting...
'predict' took 0.000564 s

Predicting...
'predict' took 0.000523 s

Predicting...
'predict' took 0.000633 s

Predicting...
'predict' took 0.000662 s

Predicting...
'predict' took 0.000475 s

Predicting...
'predict' took 0.000549 s

Predicting...
'predict' took 0.000464 s

Predicting...
'predict' took 0.000551 s

Predicting...
'predict' took 0.000551 s

Predicting...
'predict' took 0.000522 s

Predicting...
'predict' took 0.000451 s

Predicting...
'predict' took 0.000617 s

Predicting...
'predict' took 0.000472 s

Predicting...
'predict' took 0.000424 s

Predicting...
'predict' took 0.000492 s

Predicting...
'p

...

Predicting...
'predict' took 0.000541 s

Predicting...
'predict' took 0.000618 s

Predicting...
'predict' took 0.000700 s

Predicting...
'predict' took 0.000610 s

Predicting...
'predict' took 0.000577 s

Predicting...
'predict' took 0.000582 s

Predicting...
'predict' took 0.000619 s

Predicting...
'predict' took 0.000672 s

Predicting...
'predict' took 0.000599 s

Predicting...
'predict' took 0.000554 s

Predicting...
'predict' took 0.000561 s

Predicting...
'predict' took 0.000572 s

Predicting...
'predict' took 0.000606 s

Predicting...
'predict' took 0.000557 s

Predicting...
'predict' took 0.000829 s

Predicting...
'predict' took 0.000733 s

Predicting...
'predict' took 0.000644 s

Predicting...
'predict' took 0.000481 s

Predicting...
'predict' took 0.000717 s

Predicting...
'predict' took 0.000603 s

Predicting...
'predict' took 0.000517 s

Predicting...
'predict' took 0.000681 s

Predicting...
'predict' took 0.000548 s

Predicting...
'predict' took 0.000620 s

Predicting...
'p

Predicting...
'predict' took 0.000520 s

Predicting...
'predict' took 0.000582 s

Predicting...
'predict' took 0.000493 s

Predicting...
'predict' took 0.000592 s

Predicting...
'predict' took 0.000527 s

Predicting...
'predict' took 0.000450 s

Predicting...
'predict' took 0.000917 s

Predicting...
'predict' took 0.000671 s

Predicting...
'predict' took 0.000624 s

Predicting...
'predict' took 0.000639 s

Predicting...
'predict' took 0.000595 s

Predicting...
'predict' took 0.000660 s

Predicting...
'predict' took 0.000606 s

Predicting...
'predict' took 0.000601 s

Predicting...
'predict' took 0.000617 s

Predicting...
'predict' took 0.000587 s

Predicting...
'predict' took 0.052458 s

Predicting...
'predict' took 0.000705 s

Predicting...
'predict' took 0.000682 s

Predicting...
'predict' took 0.000766 s

Predicting...
'predict' took 0.000805 s

Predicting...
'predict' took 0.000872 s

Predicting...
'predict' took 0.000877 s

Predicting...
'predict' took 0.000725 s

Predicting...
'p

Predicting...
'predict' took 0.000585 s

Predicting...
'predict' took 0.000588 s

Predicting...
'predict' took 0.000767 s

Predicting...
'predict' took 0.000650 s

Predicting...
'predict' took 0.000820 s

Predicting...
'predict' took 0.000744 s

Predicting...
'predict' took 0.000585 s

Predicting...
'predict' took 0.000620 s

Predicting...
'predict' took 0.000593 s

Predicting...
'predict' took 0.000530 s

Predicting...
'predict' took 0.000687 s

Predicting...
'predict' took 0.000594 s

Predicting...
'predict' took 0.000641 s

Predicting...
'predict' took 0.000679 s

Predicting...
'predict' took 0.000824 s

Predicting...
'predict' took 0.000506 s

Predicting...
'predict' took 0.000469 s

Predicting...
'predict' took 0.000704 s

Predicting...
'predict' took 0.000476 s

Predicting...
'predict' took 0.000662 s

Predicting...
'predict' took 0.000499 s

Predicting...
'predict' took 0.000581 s

Predicting...
'predict' took 0.000508 s

Predicting...
'predict' took 0.000571 s

Predicting...
'p

Predicting...
'predict' took 0.000849 s

Predicting...
'predict' took 0.000462 s

Predicting...
'predict' took 0.000610 s

Predicting...
'predict' took 0.000514 s

Predicting...
'predict' took 0.000705 s

Predicting...
'predict' took 0.000800 s

Predicting...
'predict' took 0.000656 s

Predicting...
'predict' took 0.000687 s

Predicting...
'predict' took 0.000630 s

Predicting...
'predict' took 0.000808 s

Predicting...
'predict' took 0.000491 s

Predicting...
'predict' took 0.000579 s

Predicting...
'predict' took 0.000638 s

Predicting...
'predict' took 0.000546 s

Predicting...
'predict' took 0.000497 s

Predicting...
'predict' took 0.000509 s

Predicting...
'predict' took 0.000626 s

Predicting...
'predict' took 0.053735 s

Predicting...
'predict' took 0.000753 s

Predicting...
'predict' took 0.000583 s

Predicting...
'predict' took 0.000469 s

Predicting...
'predict' took 0.000835 s

Predicting...
'predict' took 0.000575 s

Predicting...
'predict' took 0.001073 s

Predicting...
'p

ValueError: Found array with dim 3. Estimator expected <= 2.

In [49]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])



def f(u, k, ybar):
    tic = timeit.default_timer()
    name_t = joblib.load("../results/Offline/GP_p3.pkl")
    T_mp, T_vp = name_t.predict(np.array([u,k,ybar]).reshape(1,3), eval_MSE=True)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T=T_mp[0].reshape(61,61)
    U, _ = EF(u,k,ybar)
    resPINN=T_mp[0]
    Target=U.reshape(3721,)
    z = np.polyfit(Target, resPINN, 1)
    f1 = np.poly1d(z)
    plt.scatter(Target,resPINN,color='r',label='Data')
    plt.plot(np.unique(Target),f1(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),'-',label='Y=T')
    plt.title('DeepXDE Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z[0])+'*Target+'+str(z[1]))
    plt.legend()
    plt.show()
    fig= plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('DeepXDE (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference DeepXDE-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T - U) ** 2).mean())
    print("RMSE: %f" %rmse)
    


out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

The training process using 20 samples of parameters costs around 1h.

Since the network should be recomputed for each group of parameters, the training process cost a lot of time. However the estimated results are not as good as expected.

# <a id="pod"></a>3. POD

Proper Orthogonal Decomposition or called Principal Component Analysis (PCA) is a widely used ROM method. It converts a set of observations of possibly correlated variables into a set of values of linearly uncorrelated variables -called principal components- by using an orthogonal transformation. This transformation is defined such the first principal component has the largest variance (how much the data could variate), and the succeeding components must be orthogonal to their precedent while having the highest variance.

Rewriting the PDE problem in the form below:
$$A(\xi)X(x,y)+b(\xi)=0 $$

## <a id="pod_ga"></a> 3.1 POD-Greedy Algorithm

In this section the reduced base is computed by a greddy algorithm (which is realized by Oriol). A Greedy Algorithm is based on the estimated results of each candidate at the reduced base, in each iteration the worst point is chossen and its exact solution is used to recompute the base. 


In [15]:
def computeA1(Nx,Ny,dx,dy):
    D2x=np.zeros([Nx-2,Nx-2])
    D2y=np.zeros([Ny-2,Ny-2])
    for i in range(Nx-2):
        D2x[i][i]=-2/dx**2
        D2y[i][i]=-2/dy**2
        if i>0:
            D2x[i-1][i]=1/dx**2
            D2x[i][i-1]=1/dx**2
            D2y[i-1][i]=1/dy**2
            D2y[i][i-1]=1/dy**2

    D2x[Nx-3,Nx-3] = -1/dx**2

    D2y[Nx-3,Nx-3] = -1/dy**2
    D2y[0,0] = -1/dy**2

    A1 = np.kron(D2x,np.eye(Ny-2)) + np.kron(np.eye(Nx-2),D2y)
    return A1

def computeA2(Nx,Ny,dx):
    D1x=np.zeros((Nx-2,Nx-2))
    for i in range(Nx-2):
        D1x[i][i]=1/dx
        if i>0:
            D1x[i][i-1]=-1/dx

    A2 = np.kron(D1x,np.eye(Ny-2))
    return A2

def computeb1(u,kappa,ybar,Ny, Ly, dx, y, Ti, Tleft):
    TleftBC = np.zeros((Ny-2,1))
    b1 = np.zeros((Ny-2,1))
    for i in range(1,Ny-1):
        if y[i]<Ly/3:
            TleftBC[i-1,0] = Ti
            b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
        else:
            if y[i]>2*Ly/3:
                TleftBC[i-1,0] = Ti
                b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
            else:
                TleftBC[i-1,0] = Ti+(Tleft-Ti)*(np.sin(np.pi*np.abs(y[i]-ybar)/(1/3))+1)/2
                b1[i-1,0] = -(u/dx+ kappa/dx**2)*TleftBC[i-1,0]
    return b1,TleftBC
    
def buildAdvectionDiffusionOperators(u,kappa,ybar,Nx,Ny,dx,dy, Ly, y, Ti=300, Tleft=950):
    if u<0:
        print('Error: u should be positive')
        return None
    
    b1,TleftBC= computeb1(u,kappa,ybar,Ny, Ly, dx, y, Ti, Tleft)
    b = np.vstack([b1,np.zeros(((Nx-3)*(Ny-2),1))])

    A2 = computeA2(Nx,Ny,dx)

    A1 = computeA1(Nx,Ny,dx,dy)

    A = kappa*A1-u*A2
    return A,b,TleftBC

def buildPrecomputedOperators(V,Nx,Ny,dx,dy):
    A2 = computeA2(Nx,Ny,dx)
    A1 = computeA1(Nx,Ny,dx,dy)

    Y1 = np.dot(A1,V)
    Y2 = np.dot(A2,V)

    Z1 = Y1[0:(Ny-2),:]
    Z2 = Y2[0:(Ny-2),:]

    Ar1 = np.dot(Y1.T,Y1)
    Ar2 = np.dot(Y1.T,Y2) + np.dot(Y2.T,Y1)
    Ar3 = np.dot(Y2.T,Y2)
    Ar4 = np.dot(V.T,Y1)
    Ar5 = np.dot(V.T,Y2)

    V1 = V[0:(Ny-2),:]

    return Ar1,Ar2,Ar3,Ar4,Ar5,Z1,Z2,V1

In [16]:
def POD(wComp, pComp, nComp,pMin, pMax, nPointsPerDirection,Nx,Ny):
    nSamples = 20
    nIterations = nSamples-1
    nCandidates = 1000
    pCandidate = np.dot(pMin,np.ones((1,nCandidates))) + np.random.random((nCandidates,3)).T*np.dot((pMax-pMin),np.ones((1,nCandidates)))[...,:]
    pSamples=np.zeros((3,nSamples))
    pMiddle = (pMin+pMax)/2
    pSamples[:,0]=pMiddle[:,0]
    wSamples = np.zeros(((Nx-2)*(Ny-2),nSamples))
    A,b,_ = buildAdvectionDiffusionOperators(pMiddle[0,0],pMiddle[1,0],pMiddle[2,0],Nx,Ny,dx,dy, 1, y)
    wMiddle = sp.linalg.solve(A,b)
    wSamples[:,0]= wMiddle[:,0]
    V,_,_ = sp.linalg.svd(wSamples,full_matrices=False)

    for iIteration in range(nIterations):
        Ar1,Ar2,Ar3,Ar4,Ar5,Z1,Z2,V1 = buildPrecomputedOperators(V,Nx,Ny,dx,dy)
        maxError = 0
        candidateMaxError = 0
        for iCandidate in range(nCandidates):
            b1,_ = computeb1(pCandidate[0,iCandidate],pCandidate[1,iCandidate],pCandidate[2,iCandidate],Ny, 1, dx, y, 300, 950)
            Ar = pCandidate[1,iCandidate]*Ar4 - pCandidate[0,iCandidate]*Ar5
            br = np.dot(V1.T,b1)
            q = sp.linalg.solve(Ar,br)[:,0]
            errorIndicator = np.dot(q.T,np.dot(pCandidate[1,iCandidate]**2*Ar1-pCandidate[1,iCandidate]*pCandidate[0,iCandidate]*Ar2+pCandidate[0,iCandidate]**2*Ar3,q))-2*np.dot(pCandidate[1,iCandidate]*np.dot(b1.T,Z1)-pCandidate[0,iCandidate]*np.dot(b1.T,Z2),q)+np.dot(b1.T,b1)
            if iCandidate==0 or maxError<errorIndicator:
                candidateMaxError = iCandidate
                maxError = errorIndicator

        A,b,_ = buildAdvectionDiffusionOperators(pCandidate[0,candidateMaxError],pCandidate[1,candidateMaxError],pCandidate[2,candidateMaxError],Nx,Ny,dx,dy, 1, y)
        wSamples[:,iIteration+1] = sp.linalg.solve(A,b)[:,0]
        pSamples[:,iIteration+1]=pCandidate[:,candidateMaxError]

        V,_,_ = sp.linalg.svd(wSamples[:,0:iIteration+2],full_matrices=False)

    return wSamples,pSamples,V

In [17]:
Nx = 61
Ny = 61
Lx = 1
Ly = 1
dx = Lx/(Nx-1)
dy = Ly/(Ny-1)
x = np.linspace(0,Lx,Nx)
y = np.linspace(0,Ly,Ny)
Ti = 300
Tleft = 950
pMin = np.array([[0.],[5e-5],[0.4]])
pMax = np.array([[0.5],[0.025],[0.65]])

In [33]:
# Pre-computation of candidate points
tic = timeit.default_timer()
nPointsPerDirection = 10
uComp = np.linspace(pMin[0],pMax[0],nPointsPerDirection)
kappaComp = np.linspace(pMin[1],pMax[1],nPointsPerDirection)
ybarcomp = np.linspace(pMin[2],pMax[2],nPointsPerDirection)
nComp = nPointsPerDirection**3
wComp = np.zeros(((Nx-2)*(Ny-2),nComp))
pComp = np.zeros((3,nComp))
count = 0

for ip in range(nPointsPerDirection):
    for jp in range(nPointsPerDirection):
        for kp in range(nPointsPerDirection):
            pComp[:,count] = np.hstack([uComp[ip],kappaComp[jp],ybarcomp[kp]])
            A,b,TleftBC = buildAdvectionDiffusionOperators(pComp[0,count],pComp[1,count],pComp[2,count],Nx,Ny,dx,dy, 1, y)
            #print(sp.linalg.solve(A,b).shape)
            #print(wComp[:,count])
            wComp[:,count] = sp.linalg.solve(A,b)[:,0]
            count += 1  
toc = timeit.default_timer()
print("OFFLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")

OFFLINE COMPUTATION TIME: 11.402096998283332 min


In [34]:
np.save("../results/Offline/wComp",wComp)

In [34]:
np.save("../results/Offline/wComp2",wComp)

In [19]:
wComp=np.load("../results/Offline/wComp.npy")

Once the reduced base is computed, we can transfer the real PDE problem to a reduced order model. To resolve the parametric PDE problem, serveal candidate points are uniformly choosen from the parameters' domain to feed a estimateur with Kriging interpolation.

In [36]:
def kriging_extended(wComp,pCandMax,pMin,pMax, nSamples, V):
    nParam = 3
    nLHS = 150 - nSamples
    pCandidate = np.dot(pMin,np.ones((1,nLHS))) + lhs(nParam,nLHS).T*np.dot((pMax-pMin),np.ones((1,nLHS)))
    id_cand = []
    i = 0
    for cand in pCandidate:
        for j in range(nSamples):
            rv_cand = True
            while True:
                breaker = False
                for k in range(nParam):
                    if cand[k] != pCandMax[k,j]: 
                        rv_cand = False
                        breaker = True
                        break
                    if k == nParam-1:
                        rv_cand = True
                        breaker = True
                if breaker:
                    break
            if rv_cand: id_cand.append(i)
        i += 1   
    for k in reversed(id_cand): pCandidate = np.delete(pCandidate, (k), axis=0)
    
    for iCandidate in range(np.size(pCandidate,axis=1)):
        A,b,_ = buildAdvectionDiffusionOperators(pCandidate[0,i],pCandidate[1,i],pCandidate[2,i],Nx,Ny,dx,dy, 1, y)
        Ar = np.dot(np.dot(V.T,A),V)
        br = np.dot(V.T,b)
        qr= sp.linalg.solve(Ar,br)[:,0]
        q=np.dot(V,qr)
        xsize = len(V[:,0])
        wComp = np.hstack((wComp,q.reshape(xsize,1)))
        xsize = len(pCandidate[:,iCandidate])
        p_exp = np.reshape(pCandidate[:,iCandidate],(xsize,1))
        pCandMax = np.hstack((pCandMax,p_exp))
    
    return wComp, pCandMax

In [40]:
# This is the Kriging interpolation
tic = timeit.default_timer()
wSamples,pSamples,V=POD(wComp, pComp,1000,pMin,pMax,10,Nx,Ny)
wSamples,pCandMax = kriging_extended(wSamples,pSamples,pMin,pMax, 20,V)
# Weight calculations
nLHS = len(wSamples[0,:])
nSamples=20
a_kri = np.zeros((nLHS,nSamples))
for i in range(nSamples):
    for j in range(nLHS):
        a_kri[j,i] = np.dot(wSamples[:,j].T,V[:,i])
mean = "constant"
covariance = "squared_exponential"
theta_U = np.array([100000.0]*3)
theta_L = np.array([0.001]*3)
theta_0 = np.array([1.0]*3)
for i in range(nSamples):
    GP = GaussianProcess(regr = mean, corr = covariance,theta0 = theta_0,thetaL = theta_L, thetaU = theta_U)
    GP.fit(pCandMax.T, a_kri[:,i])
    joblib.dump(GP, "../results/Offline/GP_kri_"+str(i)+".pkl")
np.save("../results/Offline/V_kri",V)     
toc = timeit.default_timer()
print("KRIGING COMPUTATION TIME: "+str((toc-tic)/60.)+" min")


KRIGING COMPUTATION TIME: 1.0436610075833264 min


In [43]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])


def f(u, k, ybar):
    V=np.load("../results/Offline/V.npy")
    tic = timeit.default_timer()
    q_mp=np.zeros((1,20))
    for i in range(20):
        name_q = joblib.load("../results/Offline/GP_kri_"+str(i)+".pkl")
        q_mp[0,i], q_vp = name_q.predict(np.array([u,k,ybar]).reshape(1,3), eval_MSE=True)
    T_pod = 0
    for i in range(20):
        T_pod += np.dot(q_mp[0,i],V[:,i])
    _,TleftBC=computeb1(u,k,ybar,Ny, 1, dx, y, 300, 950)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T_pod=np.dot(V,q_mp[0]).reshape(59,59).T
    T_pod=np.hstack([T_pod,np.array([T_pod[:,-1]]).T])
    T_pod=np.hstack([TleftBC,T_pod])
    T_pod=np.vstack([T_pod[0,:],T_pod])
    T_pod=np.vstack([T_pod,T_pod[-1,:]])
    U, _ = EF(u,k,ybar)
    
    Target=U.reshape(3721,)
    resPOD=T_pod.reshape(3721,)
    z2 = np.polyfit(Target, resPOD, 1)
    f2 = np.poly1d(z2)
    plt.scatter(Target,resPOD,color='r',label='Data')
    plt.plot(np.unique(Target),f2(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),label='Y=T')
    plt.title('POD Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z2[0])+'*Target+'+str(z2[1]))
    plt.legend()
    plt.show()
    
    fig1 = plt.figure(figsize=(15, 10))
    ax = fig1.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('POD (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    
    fig2 = plt.figure(figsize=(15, 10))
    ax = fig2.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference POD-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T_pod - U) ** 2).mean())
    print("RMSE: %f" %rmse)

out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

In [62]:
# uniformly chossen points to feed the gaussian estimator
tic = timeit.default_timer()
_,pSamples,V=POD(wComp, pComp,nComp,pMin,pMax,nPointsPerDirection,Nx,Ny)
pCand=uniform_p(pMin,pMax,20)[:,:,0]
nSamples=len(pCand)
q=np.zeros((V.shape[0],nSamples))
for i in range(nSamples):
    A,b,_ = buildAdvectionDiffusionOperators(pCand[i,0],pCand[i,1],pCand[i,2],Nx,Ny,dx,dy, 1, y)
    Ar = np.dot(np.dot(V.T,A),V)
    br = np.dot(V.T,b)
    qr= sp.linalg.solve(Ar,br)[:,0]
    q[:,i]=np.dot(V,qr)
    #w[:,i] = np.dot(V,q[:,count])
a=np.zeros((len(q[0,:]),20))
for i in range(20):
    for j in range(len(q[0,:])):
        a[j,i] = np.dot(q[:,j].T,V[:,i])
mean = "constant"
covariance = "squared_exponential"
theta_U = np.array([100000.0]*3)
theta_L = np.array([0.001]*3)
theta_0 = np.array([1.0]*3)
for i in range(20):
    GP_q = GaussianProcess(regr = mean, corr = covariance,theta0 = theta_0,thetaL = theta_L, thetaU = theta_U)
    GP_q.fit(pCand, a[:,i])
    joblib.dump(GP_q, "../results/Offline/GP"+str(i)+"_q.pkl")
np.save("../results/Offline/V",V)    
toc = timeit.default_timer()
print("TRAINING TIME: "+str((toc-tic)/60.)+" min")

TRAINING TIME: 0.5356497370999932 min


The offline computation time is mostly used to resolve the reference results (which takes 11 min), and the training time takes only around 30 minutes.

The online computation takes less than 1 sec. And it cut down around 95% of the calculation time comparing with the reference result.

In [59]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])


def f(u, k, ybar):
    V=np.load("../results/Offline/V.npy")
    tic = timeit.default_timer()
    q_mp=np.zeros((1,20))
    for i in range(20):
        name_q = joblib.load("../results/Offline/GP"+str(i)+"_q.pkl")
        q_mp[0,i], q_vp = name_q.predict(np.array([u,k,ybar]).reshape(1,3), eval_MSE=True)
    T_pod = 0
    for i in range(20):
        T_pod += np.dot(q_mp[0,i],V[:,i])
    _,TleftBC=computeb1(u,k,ybar,Ny, 1, dx, y, 300, 950)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T_pod=np.dot(V,q_mp[0]).reshape(59,59).T
    T_pod=np.hstack([T_pod,np.array([T_pod[:,-1]]).T])
    T_pod=np.hstack([TleftBC,T_pod])
    T_pod=np.vstack([T_pod[0,:],T_pod])
    T_pod=np.vstack([T_pod,T_pod[-1,:]])
    U, _ = EF(u,k,ybar)
    
    Target=U.reshape(3721,)
    resPOD=T_pod.reshape(3721,)
    z2 = np.polyfit(Target, resPOD, 1)
    f2 = np.poly1d(z2)
    plt.scatter(Target,resPOD,color='r',label='Data')
    plt.plot(np.unique(Target),f2(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),label='Y=T')
    plt.title('POD Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z2[0])+'*Target+'+str(z2[1]))
    plt.legend()
    plt.show()
    
    fig1 = plt.figure(figsize=(15, 10))
    ax = fig1.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('POD (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    
    fig2 = plt.figure(figsize=(15, 10))
    ax = fig2.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference POD-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T_pod - U) ** 2).mean())
    print("RMSE: %f" %rmse)

out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

## <a id="tf1"></a> 3.2 POD with TensorFlow - Gaussian Process

This time the reduced base used in POD is computed by TensorFlow. The TensorFlow solve the SVD with 1000 observation. The reduced base corresponding to the biggest 20 sigular value (which takes 99% of information) is choosen. Then the problem is sovled in the reduced base with 20 groups of randomly chossen parameters in a $61\times 61$ mesh. The results are used to fit the estimator using Kriging interpolation.

In [2]:
wComp=np.load("../results/Offline/wComp.npy")

In [60]:
tic = timeit.default_timer()
s,u,v=tf.svd(wComp)
sigma=tf.diag(s)
with tf.Session() as sess:
    s,u,v=sess.run([s,u,v])

idxCand=np.random.randint(0,high=1000,size=20,dtype=int)
pMin = np.array([[0],[0.00005],[0.4]])
pMax = np.array([[0.5],[0.025],[0.65]])
V=u[:,:20]

pCand=uniform_p(pMin,pMax,20)[:,:,0]
nSamples=len(pCand)
q=np.zeros((V.shape[0],nSamples))
for i in range(nSamples):
    A,b,_ = buildAdvectionDiffusionOperators(pCand[i,0],pCand[i,1],pCand[i,2],Nx,Ny,dx,dy, 1, y)
    Ar = np.dot(np.dot(V.T,A),V)
    br = np.dot(V.T,b)
    qr= sp.linalg.solve(Ar,br)[:,0]
    q[:,i]=np.dot(V,qr)
    i+=1
a=np.zeros((len(q[0,:]),nSamples))
for i in range(20):
    for j in range(len(q[0,:])):
        a[j,i] = np.dot(q[:,j].T,V[:,i])
mean = "constant"
covariance = "squared_exponential"
theta_U = np.array([100000.0]*3)
theta_L = np.array([0.001]*3)
theta_0 = np.array([1.0]*3)
for i in range(nSamples):
    GP_q = GaussianProcess(regr = mean, corr = covariance,theta0 = theta_0,thetaL = theta_L, thetaU = theta_U)
    GP_q.fit(pCand, a[:,i])
    joblib.dump(GP_q, "../results/Offline/GP_tf"+str(i)+"_q.pkl")
np.save("../results/Offline/V_tf1",V)
toc = timeit.default_timer()
print("TRAINING TIME: "+str((toc-tic)/60.)+" min")

TRAINING TIME: 0.29197440901666594 min


Without the iterations for greedy algorithm, the training time can be 10 sec faster.


The online computation takes less than 1 sec. And it cut down around 95% of the calculation time comparing with the reference result. (It's the same with the POD-greedy algorithme because they use the same estimater.)

Since the reduced base is chossen by limiting the information loss, the prediction results can be a little bit better than the POD with Greedy Algorithm. 

In [61]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])



def f(u, k, ybar):
    V=np.load("../results/Offline/V_tf1.npy")
    tic = timeit.default_timer()
    q_mp=np.zeros((1,20))
    for i in range(20):
        name_q = joblib.load("../results/Offline/GP_tf"+str(i)+"_q.pkl")
        q_mp[0,i], q_vp = name_q.predict(np.array([u,k,ybar]).reshape(1,3), eval_MSE=True)
    T_pod = 0
    for i in range(20):
        T_pod += np.dot(q_mp[0,i],V[:,i])
    _,TleftBC=computeb1(u,k,ybar,Ny, 1, dx, y, 300, 950)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T_pod=np.dot(V,q_mp[0]).reshape(59,59).T
    T_pod=np.hstack([T_pod,np.array([T_pod[:,-1]]).T])
    T_pod=np.hstack([TleftBC,T_pod])
    T_pod=np.vstack([T_pod[0,:],T_pod])
    T_pod=np.vstack([T_pod,T_pod[-1,:]])
    U, _ = EF(u,k,ybar)
    
    Target=U.reshape(3721,)
    resPOD=T_pod.reshape(3721,)
    z2 = np.polyfit(Target, resPOD, 1)
    f2 = np.poly1d(z2)
    plt.scatter(Target,resPOD,color='r',label='Data')
    plt.plot(np.unique(Target),f2(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),label='Y=T')
    plt.title('POD Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z2[0])+'*Target+'+str(z2[1]))
    plt.legend()
    plt.show()
    
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('POD_tf (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_pod-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference POD_tf-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T_pod - U) ** 2).mean())
    print("RMSE: %f" %rmse)

out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

## <a id="tf2"></a> 3.3 POD with TensorFlow - Similarity Criterion Estimation

In this section, the resolution of a parameterized PDE problem is completly realized by TensorFlow. First, at the training step, a reduced base is constructed based on 1000 observations (the PDE results of 1000 groups of parameters $\mathbf{\xi}$):

$$\mathbf{X}=[X_0,...,X_{999}]=U\Sigma V$$

The corresponding coefficients to transport the reduced base results to real base results are also computed:

$$\mathbf{X_r}=[X_{r0},...,X_{r999}]=U^{-1}\mathbf{X} \textrm{, where } X_i=X_{ri}U \textrm{ for } 0\leq i<1000$$

In [57]:
wComp=np.load("../results/Offline/wComp.npy")

In [43]:
Nx = 61
Ny = 61
Lx = 1
Ly = 1
dx = Lx/(Nx-1)
dy = Ly/(Ny-1)
x = np.linspace(0,Lx,Nx)
y = np.linspace(0,Ly,Ny)
Ti = 300
Tleft = 950
pMin = np.array([[0],[5e-5],[0.4]])
pMax = np.array([[0.5],[0.025],[0.65]])
pComp = np.zeros((3,1000))
count = 0
nPointsPerDirection=10
uComp = np.linspace(pMin[0],pMax[0],nPointsPerDirection)
kappaComp = np.linspace(pMin[1],pMax[1],nPointsPerDirection)
ybarcomp = np.linspace(pMin[2],pMax[2],nPointsPerDirection)
for ip in range(nPointsPerDirection):
    for jp in range(nPointsPerDirection):
        for kp in range(nPointsPerDirection):
            pComp[:,count] = np.hstack([uComp[ip],kappaComp[jp],ybarcomp[kp]])
            count += 1
np.save("../results/Offline/pComp",pComp)

In [55]:
tic = timeit.default_timer()
data=tf.placeholder("float")
mean_tensor = tf.reduce_mean(data, axis=1,keep_dims=True)
mean_centered_data = tf.subtract(data,mean_tensor)
svd_out = tf.svd(mean_centered_data, compute_uv=True, full_matrices=False, name="svd")
with tf.Session() as sess:
    mean=sess.run(mean_tensor,feed_dict={data:wComp})
    s, V, v = sess.run(svd_out,feed_dict={data:wComp})
    coeffs = sess.run(tf.matmul(tf.transpose(V), mean_centered_data),feed_dict={data:wComp})
np.save("../results/Offline/meanT",mean)
np.save("../results/Offline/V_tf2",V)
np.save("../results/Offline/coeffs",coeffs)
toc = timeit.default_timer()
print("TRAINING TIME: "+str((toc-tic)/60.)+" min")

TRAINING TIME: 0.03625490466665724 min


In this method, only the parameters and the computational results in the observation set are needed. And it's not necessary to know the structure of the real PDE system. It means that we can realize the estimation of a black box system just by a group of observations. 

Since the results are computed based on the existing observations, the number of observations has a great influence on the prediction precision. And the prediction works very well when the new parameters are closed to the parameters in the observation set. However, when these parameters are not in the observation set, the precision becomes worse.

For a group of parameters $\xi^*$ which is not in the observation set, the coefficient $X_r^*$ is estimated by a similarity criterion. And here the cosine similarity index is used:

$$X_r^*=X_{r\xi_k}+(X_{r\xi_{k+1}}-X_{r\xi_k})\frac{\xi^*-\xi_k}{\xi_{k+1}-\xi_k} \textrm{, where } \xi_k<\xi^*<\xi_{k+1}$$

In [56]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

def predict(params,pMax,pMin,n,coeffs,u,pComp):
    pL=(pMax-pMin)/(n-1)
    ip=int((params[0]-pMin[0])//pL[0][0])
    jp=int((params[1]-pMin[1])//pL[1][0])
    kp=int((params[2]-pMin[2])//pL[2][0])
    k=ip*100+jp*10+kp
    if ip<9:ip+=1
    if jp<9:jp+=1
    if kp<9:kp+=1
    k_1=ip*100+jp*10+kp
    if(params.reshape(1,3) in pComp):
        return np.dot(u,coeffs[:,k])

    t1 = tf.reduce_sum(params.T-pComp[:,k:k+1])
    t2 = tf.reduce_sum(pComp[:,k_1:k_1+1]-pComp[:,k:k+1])
    with tf.Session() as sess:
        delta = sess.run(tf.div(t1, t2, name="delta"))
    coeff=coeffs[:,k]+(coeffs[:,k_1]-coeffs[:,k])*delta
    res=np.dot(u,coeff)
    return res

The online computation takes less than 1 sec. And it cut down around 87%-97% (depends on whether the new group of parameters is in the observation set or not) of the calculation time comparing with the reference result.

In [57]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])


def f(u, k, ybar):
    pMin = np.array([[0],[0.00005],[0.4]])
    pMax = np.array([[0.5],[0.025],[0.65]])
    coeffs=np.load("../results/Offline/coeffs.npy")
    pComp=np.load("../results/Offline/pComp.npy")
    mean=np.load("../results/Offline/meanT.npy")
    V=np.load("../results/Offline/V_tf2.npy")
    tic = timeit.default_timer()
    T_tf=predict(np.array([u,k,ybar]),pMax,pMin,10,coeffs,V,pComp)
    T_tf=T_tf+mean.T
    _,TleftBC=computeb1(u,k,ybar,Ny, 1, dx, y, 300, 950)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T_tf=T_tf.reshape(59,59).T
    T_tf=np.hstack([T_tf,np.array([T_tf[:,-1]]).T])
    T_tf=np.hstack([TleftBC,T_tf])
    T_tf=np.vstack([T_tf[0,:],T_tf])
    T_tf=np.vstack([T_tf,T_tf[-1,:]])
    U, _ = EF(u,k,ybar)
    
    Target=U.reshape(3721,)
    resPOD=T_tf.reshape(3721,)
    z2 = np.polyfit(Target, resPOD, 1)
    f2 = np.poly1d(z2)
    plt.scatter(Target,resPOD,color='r',label='Data')
    plt.plot(np.unique(Target),f2(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),label='Y=T')
    plt.title('POD Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z2[0])+'*Target+'+str(z2[1]))
    plt.legend()
    plt.show()
    
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_tf, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('POD_tf (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    
    fig = plt.figure(figsize=(15, 10))
    ax = fig.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_tf-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference POD_tf-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T_tf - U) ** 2).mean())
    print("RMSE: %f" %rmse)

out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

# <a id="gp"></a> 4. Gaussian Process

In [2]:
wComp=np.load("../results/Offline/wComp.npy")
pComp=np.load("../results/Offline/pComp.npy")

In [4]:
pComp.shape

(3, 1000)

In [7]:
tic = timeit.default_timer()
mean = "constant"
covariance = "squared_exponential"
theta_U = np.array([100000.0]*3)
theta_L = np.array([0.001]*3)
theta_0 = np.array([1.0]*3)
GP = GaussianProcess(regr = mean, corr = covariance,theta0 = theta_0,thetaL = theta_L, thetaU = theta_U)
GP.fit(pComp.T, wComp.T)
joblib.dump(GP, "../results/Offline/GP_p.pkl")
    
toc = timeit.default_timer()
print("OFFLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")

OFFLINE COMPUTATION TIME: 0.6396421524666664 min


In [13]:
# IF YOU WANT TO SEE THE PREDICTION RESULT, PLEASE LAUNCH THIS SECTION

u = ipywidgets.FloatSlider(value=0.11,min=0,max=0.5,step=0.01,description='u:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
k = ipywidgets.FloatSlider(value=0.025,min=0,max=0.025,step=0.00005,description='k:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.5f',)
ybar = ipywidgets.FloatSlider(value=0.4,min=0.4,max=0.65,step=0.01,description='y_bar:',
                           disabled=False,continuous_update=False,orientation='horizontal',
                           readout=True,readout_format='.2f',)
ui = ipywidgets.HBox([u, k, ybar])


def f(u, k, ybar):
    tic = timeit.default_timer()
    name_t = joblib.load("../results/Offline/GP_p.pkl")
    T_mp, T_vp = name_t.predict(np.array([u,k,ybar]).reshape(1,3), eval_MSE=True)
    _,TleftBC=computeb1(u,k,ybar,Ny, 1, dx, y, 300, 950)
    toc = timeit.default_timer()
    print("ONLINE COMPUTATION TIME: "+str((toc-tic)/60.)+" min")
    T_gp=T_mp.reshape(59,59).T
    T_gp=np.hstack([T_gp,np.array([T_gp[:,-1]]).T])
    T_gp=np.hstack([TleftBC,T_gp])
    T_gp=np.vstack([T_gp[0,:],T_gp])
    T_gp=np.vstack([T_gp,T_gp[-1,:]])
    U, _ = EF(u,k,ybar)
    
    Target=U.reshape(3721,)
    res=T_gp.reshape(3721,)
    z2 = np.polyfit(Target, res, 1)
    f2 = np.poly1d(z2)
    plt.scatter(Target,res,color='r',label='Data')
    plt.plot(np.unique(Target),f2(np.unique(Target)),label='F')
    plt.plot(np.unique(Target),np.unique(Target),label='Y=T')
    plt.title('GP Test (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.xlabel('Target')
    plt.ylabel('Output~='+str(z2[0])+'*Target+'+str(z2[1]))
    plt.legend()
    plt.show()
    
    fig1 = plt.figure(figsize=(15, 10))
    ax = fig1.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_gp, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('GP (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    
    fig2 = plt.figure(figsize=(15, 10))
    ax = fig2.add_subplot(111)
    ax.set_yticklabels(np.linspace(0,1,0.1))
    ax.set_xticklabels(np.linspace(0,1,0.1))
    im = ax.imshow(T_gp-U, cmap=plt.cm.hot_r)
    plt.colorbar(im)
    plt.legend()
    plt.title('difference GP-reference (u='+str(u)+', k='+str(k)+', ybar='+str(ybar)+')')
    plt.show()
    rmse=np.sqrt(((T_gp - U) ** 2).mean())
    print("RMSE: %f" %rmse)

out = ipywidgets.interactive_output(f, {'u': u, 'k': k, 'ybar': ybar})

display(ui, out)

Output()

# References
1. LU LU, XUHUI MENG, ZHIPING MAO, and GEORGE EM KARNIADAKIS. DEEPXDE: A DEEP LEARNING LIBRARY FOR SOLVING DIFFERENTIAL EQUATIONS.
2. Sunil Suram. Reduced Order Modeling using TensorFlow.
3. Sunil Suram, Kenneth M. Bryden. Integrating a reduced-order model server into the engineering designprocess.  Advances in Engineering Software 90 (2015) 169–182.